In [175]:
import csv                               # csv reader
import re
from sklearn.svm import LinearSVC
from nltk.classify import SklearnClassifier
from random import shuffle
from sklearn.pipeline import Pipeline
from sklearn.metrics import precision_recall_fscore_support

In [176]:
# load data from a file and append it to the rawData
def loadData(path, Text=None):
    with open(path,encoding = 'utf8') as f:
        reader = csv.reader(f, delimiter='\t')
        for line in reader:
            if line[0] == "DOC_ID":  # skip the header
                continue
            (Id, Text, Label) = parseReview(line)
            rawData.append((Id, Text, Label))


def splitData(percentage):
    # A method to split the data between trainData and testData 
    dataSamples = len(rawData)
    halfOfData = int(len(rawData)/2)
    trainingSamples = int((percentage*dataSamples)/2)
    for (_, Text, Label) in rawData[:trainingSamples] + rawData[halfOfData:halfOfData+trainingSamples]:
        trainData.append((toFeatureVector(preProcess(Text)),Label))
    for (_, Text, Label) in rawData[trainingSamples:halfOfData] + rawData[halfOfData+trainingSamples:]:
        testData.append((toFeatureVector(preProcess(Text)),Label))

# Label information

In [177]:
# Convert line from input file into an id/text/label tuple
def parseReview(reviewLine):
    # Should return a triple of an integer, a string containing the review, and a string indicating the label
    # DESCRIBE YOUR METHOD IN WORDS
        Id = reviewLine[0] # Id should equal the first colum of reviewLine 
        Text = reviewLine[8] # Text should equal the last colum of reviewLine 
        Label = reviewLine[1] # Label should equal the second colum of reviewLine 
        return (Id, Text, Label) # return the value

In [178]:
# TEXT PREPROCESSING AND FEATURE VECTORIZATION

# Input: a string of one review
def preProcess(text):
    # Should return a list of tokens
    # DESCRIBE YOUR METHOD IN WORDS
     # word tokenisation
    text = re.sub(r"(\w)([.,;:!?'\"”\)])", r"\1 \2", text) # this process will tokenise or split punctuation in sentence.
    text = re.sub(r"([.,;:!?'\"“\(])(\w)", r"\1 \2", text) # this process will tokenise or split punctuation in sentence.
    print("tokenising:", text) # test the code by printing
    tokens = re.split(r"\s+",text) # store the result from tokenisation process in "tokens"
    # normalisation
    text = re.sub(r"(\S)\1\1+",r"\1\1\1", text) 
    tokens = [t.lower() for t in tokens] # this process will normalise the sentence from tokenisation process in order to separate in word by word
    return tokens # return the parameter

# Feature engineering

In [179]:
featureDict = {} # A global dictionary of features

def toFeatureVector(tokens):
    # Should return a dictionary containing features as keys, and weights as values
    # DESCRIBE YOUR METHOD IN WORDS
    d = {} # create the variable "d" to store dictionary and set it to empty dictionary
    for w in tokens:
        try: # try the loop from tokens
            i = featureDict[w] # add the value in dictionary
        except KeyError: # if it has error, it will run the code at below
            i = len(featureDict) + 1 # store the value in i
            featureDict[w] = i # add new word in dictionary
        try:
            d[i] += (1.0/len(tokens)) #store new value from featureDict to new dictionary as d by adding the previous value
        except KeyError: # if it has error, it will run the code at below
            d[i] = (1.0/len(tokens)) # store value in new dictionary "d"
        return d

In [180]:
toFeatureVector(["hello", "to"])

{1: 0.5}

In [181]:
# TRAINING AND VALIDATING OUR CLASSIFIER
def trainClassifier(trainData):
    print("Training Classifier...")
    pipeline =  Pipeline([('svc', LinearSVC())])
    return SklearnClassifier(pipeline).train(trainData)

# Cross validation

In [182]:
def crossValidate(dataset, folds):
    shuffle(dataset)
    cv_results = []
    foldSize = int(len(dataset)/folds)
    # DESCRIBE YOUR METHOD IN WORDS
    for i in range(0,len(dataset),foldSize):
        #continue # Replace by code that trains and tests on the 10 folds of data in the dataset
        tr_x = dataset[i : i + foldSize] # tr_x is the fold for testing
        train_data = dataset[0 : i] + dataset[foldSize : ]   # the training data which is the rest of dataset
        classifier = trainClassifier(train_data)  # train the data in classifier
        trainPred = predictLabels(tr_x, classifier)  # classify the test data to get predicted labels
        trainTrue = list(map(lambda t: t[1], tr_x)) # classify the test data to get true labels
        before_results = list(precision_recall_fscore_support(trainTrue, trainPred, average='weighted')) # find the precision, recall and f-score and store in before_results
        cv_results.append(before_results) # collect the result in cv_results
    return cv_results

In [183]:
# PREDICTING LABELS GIVEN A CLASSIFIER

def predictLabels(reviewSamples, classifier):
    return classifier.classify_many(map(lambda t: t[0], reviewSamples))

def predictLabel(reviewSample, classifier):
    return classifier.classify(toFeatureVector(preProcess(reviewSample)))

In [215]:
# MAIN

# loading reviews
# initialize global lists that will be appended to by the methods below
rawData = []          # the filtered data from the dataset file (should be 21000 samples)
trainData = []        # the pre-processed training data as a percentage of the total dataset (currently 80%, or 16800 samples)
testData = []         # the pre-processed test data as a percentage of the total dataset (currently 20%, or 4200 samples)

# the output classes
fakeLabel = 'fake'
realLabel = 'real'

# references to the data files
reviewPath = 'amazon_reviews.txt'

# Do the actual stuff (i.e. call the functions we've made)
# We parse the dataset and put it in a raw data list
print("Now %d rawData, %d trainData, %d testData" % (len(rawData), len(trainData), len(testData)),
      "Preparing the dataset...",sep='\n')
loadData(reviewPath) 

# We split the raw dataset into a set of training data and a set of test data (80/20)
# You do the cross validation on the 80% (training data)
# We print the number of training samples and the number of features before the split
print("Now %d rawData, %d trainData, %d testData" % (len(rawData), len(trainData), len(testData)),
      "Preparing training and test data...",sep='\n')
splitData(0.8)
# We print the number of training samples and the number of features after the split
print("After split, %d rawData, %d trainData, %d testData" % (len(rawData), len(trainData), len(testData)),
      "Training Samples: ", len(trainData), "Features: ", len(featureDict), sep='\n')

# QUESTION 3 - Make sure there is a function call here to the
# crossValidate function on the training set to get your results
crossValidate(trainData, 10)





Now 0 rawData, 0 trainData, 0 testData
Preparing the dataset...
Now 21000 rawData, 0 trainData, 0 testData
Preparing training and test data...
tokenising: When least you think so , this product will save the day . Just keep it around just in case you need it for something .
tokenising: Lithium batteries are something new introduced in the market there average developing cost is relatively high but Stallion doesn ' t compromise on quality and provides us with the best at a low cost .<br />There are so many in built technical assistants that act like a sensor in their particular forté . The battery keeps my phone charged up and it works at every voltage and a high voltage is never risked .
tokenising: I purchased this swing for my baby . She is 6 months now and has pretty much out grown it . It is very loud and doesn ' t swing very well . It is beautiful though . I love the colors and it has a lot of settings , but I don ' t think it was worth the money .
tokenising: I was looking for an

tokenising: I was just on  the Internet a few weeks ago and heard complaints about these chinese water ionizers .  These are the Aqua Ionizer by Air , Water and Life that are supposed to be made in the USA but are really made in China .  I bought my unit about 8 months ago and we used it for a while but really didn ' t notice any difference in our health .  We are active people in our late 40 ' s and we are always looking for ways to make us healthy .  We have read a lot about what to look for an this company , Real Spirit , put on the Internet that the machine was top of the line at a low price .  We bought it based on this information and after trying it we stopped using it because of the lack of results .  A friend of my  Wife ' s was over the other day and when we were talking , this subject came up .  He showed us a bunch of negative stuff online and we realized we fell for this scam .  He also showed us some other company ' s products and said they were certified by a USA water q

tokenising: For only this is a very great scope , and very Accurate once you get done with the hassle of Sighting it in , but Overall I love it and would Definitely recommend this to a friend an only 4 stars because you can always Improve on something
tokenising: I choose probotics because I would often see ads and commercial on how probotics where good for your health however after taking probotics for 7 days  i have a felt no changes in my bowels or the way i felt , I am saying that i did not dislike the product I am saying that probotics did nothing to improve myself .<br />i would recommend probotics to anyone who is willing to give it a try it might help them , but it did not work for me .
tokenising: Great book . I enjoyed this book . Brilliance is an exciting &#34 ; futuristic&#34 ; story that could easily have taken place today . A fun read , can ' t wait to start the 2nd novel .
tokenising: My son loved Dora so much that I decided to support and encourage his interest . Compar

tokenising: Took the poles out for the first time this Saturday and already one of the poles has broken . They are cheap and cheaply made , will be returned Monday morning for something of better quality .
tokenising: I could barely tolerate the taste and texture of these wraps and I ' m usually a very tolerant person who can eat anything . Once , I ate an entire plate of pasta that was both burned and uncooked . I could not figure out how that happened , even now .
tokenising: My daughter had a problem getting my grandson to eat his veggies . At one of his checkups the doctor did a blood test . We were told his iron was low , because lack of veggies in his diet . I bought her some of the food products , he just loved them .
tokenising: This was a pretty far-fetched piece of work , and that ' s putting it mildly . If I look at it as a form of entertainment , I supposed it works . But I have a feeling that that ' s not what the author intended .
tokenising: My husband has long , thin fi

tokenising: When I tried it on my phone it didn ' t fit quite well . I have to take it off and put on my old one back .
tokenising: You will need speakers for sure for this TV . I had to return it , just did not work for my needs . And it was for my kitchen and it still wasn ' t of good quality enough . Order this for an on-suite bathroom in a small space or a small home-office .
tokenising: My wife first got a pair of these golf shoes and was bragging how light they were . I have trouble with my feet so thought I would try them out . They are as light and comfortable as she said . I may even buy another pair .
tokenising: Stability balls are , well , stability balls . What makes this one different is it has a little sand in the bottom so the ball does not roll away when you get up . This is a simple and low cost modification does give it an edge over those that do not .
tokenising: Ok this is one of those products you get what you pay for . They quality is awful so don ' t waste your 

...

tokenising: Solid book .  Clear and appropriate fundamentals , and helpful detailed tools , to get your company focused on generating maximum return .  I read it before I had to and I couldn ' t be happier I did .  Well written .
tokenising: this is nice to have but I have already had to superglue it together at the center where all the slats connect so I was not real happy about that .
tokenising: This is such a nice rich fragrance that is no longer available in the brick and mortar stores . Thank God I can get it on Amazon .
tokenising: BAD BAD BAD PRODUCT , ONLY GOOD FOR 2 MONTHS AFTER THAT OUT . DO NOT FALL FOR LOW PRICE , THIS IS BAD PRODUCT . BUY THE ORIGINAL ONE AND WILL LAST YOU FOR 1 TO 2 YEARS .
tokenising: Have purchased watches on-line before but been disappointed . This one however is genuine and is a very classy watch . The watch face glass is curved which ( i think ) gives it a really classy look . Nice size too , very happy with my purchase . Recommend .
tokenising: Ori

tokenising: These stylus , s work great on my iPad Air - even with a protective sheet that I put on . I use it with Notes Plus and INKredible very well . The two lanyards are of perfect length and gets out of the way when I write . One improvement could be a way to store this stylus with a snap cover . Perhaps a metal sheath ( removable ) would allow the pen to be placed in the side when not in use ?<br /><br />I recommend this and will buy more !
tokenising: Amazing purchase . It looks exactly like the $200 ring my husband liked in the store and this is even a much better quality material . He loves how it looks , and I don ' t have to stress about him losing it ( bc it is very likely to happen ) He has bumped it a few times and it had yet to scratch .
tokenising: I ' m a book devourer .  ( is that a word ?  gee - i should know that !)  And i read many different types .<br /><br />Over my lifetime ( i ' m 53 ), i believe i ' ve read thousands .  I love books , and rarely hate one .  I

tokenising: As others have mentioned the author is quite candid throughout the book . Brutally honest in fact At the same time it is very depressing and difficult to read . Just another talent chewwed up by drugs and Hollywood . Would like to be optimistic about his future but very hard to be . The book ends pretty abrubtly
tokenising: Este libro aporta gran conocimiento bíblico , social e histórico que ayuda a desarrollar un estudio más profundo y a tener una mejor comprensión de estas dos epístolas , ¡Valiosisimo libro para impartir estudios bíblicos !
tokenising: My wife got me this for christmas and I ' m so happy with it . After initial setup the Xbox and Kinect are a great pair . I originally didn ' t want the Kinect but I ' ve found its pretty cool and probably will have some cool uses down the road . My Xbox did slow down and freeze during downloads so I suggest only downloading one game or thing at a time . I was doing six and it was clearly too much . That being said it runs 

tokenising: I love these boots , easy to put on , easy to remove , not too warm . They fit great ! I have problems with my feet , and shoes are always too tight .. but these are perfect !! LOve LOVE LOVE
tokenising: Its easy to overlook these sunglasses nowadays but hey , there ' s a reason everyone has them ! First off , I ordered these at 4 PM on Friday and they showed up at 11 AM Saturday morning ! Amazon is awesome , if its available through Amazon I choose to order through Amazon for easier returns , etc . and still only $83 + $3 shipping upgrade ! Way better than going into a sunglass store , but still Ray-Ban .<br />On the glasses themselves : They do fit a little snug , perhaps its the size I ordered but they don ' t squeeze my head or bother me at all so I ' m fine . They ' re heavy-weight , quality glasses . You can tell they ' re Ray-Ban and they ' re worth the money . Holding and wearing these makes you realize that cheap sunglasses don ' t always cut it , unless you ' re a

Training Classifier...
Training Classifier...
Training Classifier...
Training Classifier...
Training Classifier...
Training Classifier...
Training Classifier...
Training Classifier...
[[0.532585110362888, 0.5291666666666667, 0.5214946425092538, None], [0.5647797505447639, 0.5636904761904762, 0.5580041935858397, None], [0.5726487642528001, 0.5672619047619047, 0.5596446421884106, None], [0.5801433639176357, 0.5732142857142857, 0.567741131932461, None], [0.5295349314071781, 0.5291666666666667, 0.5249142719149964, None], [0.5283590502360318, 0.5273809523809524, 0.5232703755167859, None], [0.5663071108163635, 0.5625, 0.5580417374848873, None], [0.5693421637048861, 0.5666666666666667, 0.563045108753884, None], [0.5503723481743834, 0.5476190476190477, 0.5416961903736479, None], [0.5629458380574452, 0.5625, 0.5581166444000107, None]]


# Evaluate on test set

In [185]:
# Finally, check the accuracy of your classifier by training on all the tranin data
# and testing on the test set
# Will only work once all functions are complete
functions_complete = True# set to True once you're happy with your methods for cross val
if functions_complete:
    print(testData[0])   # have a look at the first test data instance
    classifier = trainClassifier(trainData)  # train the classifier
    testTrue = [t[1] for t in testData]   # get the ground-truth labels from the data
    testPred = predictLabels(testData, classifier)  # classify the test data to get predicted labels
    finalScores = precision_recall_fscore_support(testTrue, testPred, average='weighted') # evaluate
    print("Done training!")
    print("Precision: %f\nRecall: %f\nF Score:%f" % finalScores[:3])

({9: 0.04}, '__label1__')
Training Classifier...
Done training!
Precision: 0.547544
Recall: 0.545714
F Score:0.541300


# Optimization
improve preProcess, parseReview, split_data

In [211]:
#Question 4
# we will improve pre processing by using lemmatisation and stemming 

from nltk.stem.porter import PorterStemmer #import stemming methodology
from nltk.stem import WordNetLemmatizer #import lemmatizer

def preProcess_improve(text, rating, verifyPurchase, prod_ID): # define preProcess_improve before anlyse the data by using tokenisation, 
    #normalisation, lemmatisation, and stemming
    
     # word tokenisation
    text = re.sub(r"(\w)([.,;:!?'\"”\)])", r"\1 \2", text) # this process will tokenise or split punctuation in sentence.
    text = re.sub(r"([.,;:!?'\"“\(])(\w)", r"\1 \2", text) # this process will tokenise or split punctuation in sentence.
    print("tokenising:", text) # test the code by printing
    tokens = re.split(r"\s+",text) # store the result from tokenisation process in "tokens"
    # normalisation
    text = re.sub(r"(\S)\1\1+",r"\1\1\1", text) 
    tokens = [t.lower() for t in tokens] # this process will normalise the sentence from tokenisation process in order to separate in word by word
    
    stemmer = PorterStemmer() # using stemming process and store in stemmer
    lemmatizer = WordNetLemmatizer() # using lemmatisation process and store in lemmatizer
    new_tokens = stemmer.stem(lemmatizer.lemmatize(tokens)) # generate new_tokens by using stemming after lemmatisation
    
    
    return (new_tokens,rating, verifyPurchase, prod_ID) # return the parameter



In [218]:
#Question5
# we will pick rating, VERIFIED_PURCHASE and PRODUCT_ID to increase efficiency because these parameters have involvement among the reviewText 
# so these variables would made more precision in the model

def parseReview_improve(reviewLine):
        Id = reviewLine[0] # Id should equal the first colum of reviewLine 
        Text = reviewLine[8] # Text should equal the last colum of reviewLine 
        Label = reviewLine[1] # Label should equal the second colum of reviewLine 
        rating = reviewLine[2] # rating should equal the third colum of reviewLine
        verifyPurchase = reviewLine[3] # product category should equal the forth colum of reviewLine that is VERIFIED_PURCHASE
        prod_ID = reviewLine[5] # product title should equal the sixth colum of reviewLine that is PRODUCT_ID
        return (Id, Text, Label, rating, verifyPurchase, prod_ID) # return the value


def loadData_improve(path, Text=None): # define loadData_improve for adding rating, verifyPurchase, prod_ID in the data
    with open(path,encoding = 'utf8') as f:
        reader = csv.reader(f, delimiter='\t')
        for line in reader:
            if line[0] == "DOC_ID":  # skip the header
                 continue
            (Id, Text, Label, rating, verifyPurchase, prod_ID) = parseReview_improve(line) 
            rawData.append((Id, Text, Label,  rating, verifyPurchase, prod_ID)) # add these parameters into rawData
                     
def splitData_improve(percentage): # define splitData_improve for improving splitData function by adding rating, verifyPurchase and prod_ID into the train and test data
    
      dataSamples = len(rawData)
      halfOfData = int(len(rawData)/2)
      trainingSamples = int((percentage*dataSamples)/2)
      for (_,Text, rating,verifyPurchase, prod_ID, Label) in rawData[:trainingSamples] + rawData[halfOfData:halfOfData+trainingSamples]:
          trainData.append((toFeatureVector(preProcess_improve(Text, rating, verifyPurchase, prod_ID)),Label)) #adding train dataset which include Text, rating,
                                                                                                                                                           #verify_Purchase, prod_ID
      for (_,Text, rating, verifyPurchase, prod_ID, Label) in rawData[trainingSamples:halfOfData] + rawData[halfOfData+trainingSamples:]:
          testData.append((toFeatureVector(preProcess_improve(Text, rating, verifyPurchase, prod_ID)),Label)) # adding test dataset which include Text, rating,
                                                                                                                                                          # verify_Purchase, prod_ID
        
reviewPath = 'amazon_reviews.txt'
        
loadData_improve(reviewPath) #load data

splitData_improve(0.8) # split the data in 80% training 




crossValidate(trainData, 10) # run the cross validation

[[0.532585110362888, 0.5291666666666667, 0.5214946425092538, None], [0.5647797505447639, 0.5636904761904762, 0.5580041935858397, None], [0.5726487642528001, 0.5672619047619047, 0.5596446421884106, None], [0.5801433639176357, 0.5732142857142857, 0.567741131932461, None], [0.5295349314071781, 0.5291666666666667, 0.5249142719149964, None], [0.5283590502360318, 0.5273809523809524, 0.5232703755167859, None], [0.5663071108163635, 0.5625, 0.5580417374848873, None], [0.5693421637048861, 0.5666666666666667, 0.563045108753884, None], [0.5503723481743834, 0.5476190476190477, 0.5416961903736479, None], [0.5629458380574452, 0.5625, 0.5581166444000107, None]]
